In [1]:
# 
# %%time

import requests
import pandas as pd
import psycopg2

all_data = []
start_offset = 0
url = "https://api.eia.gov/v2/electricity/rto/region-data/data/?frequency=hourly&data[0]=value&sort[0][column]=period&sort[0][direction]=desc&offset=0&length=0&api_key=q5n29GJXkd5xd0nznZ9ZSfLwUSfA70oUP2WLaZhy"

response = requests.get(url)
json_data = response.json()

total_record = 11000 #int(json_data['response']['total'])


db_params = {
    'dbname': 'reliance',
    'user': 'docker',
    'password': 'docker',
    'host': "192.168.1.188",#'192.168.1.223',#"192.168.29.101",#
    'port': 5432
}


conn = psycopg2.connect(**db_params)

cur = conn.cursor()

create_table_query = '''
CREATE TABLE IF NOT EXISTS elec_api_data (
    period TIMESTAMP,
    respondent TEXT,
    respondent_name TEXT,
    type TEXT,
    type_name TEXT,
    value BIGINT,
    value_units TEXT
);
'''

cur.execute(create_table_query)
conn.commit()
print("Table created")

insert_query = '''
INSERT INTO elec_api_data (period, respondent, respondent_name, type, type_name, value, value_units)
VALUES (%s, %s, %s, %s, %s, %s, %s)
'''


while start_offset < total_record:
    url = f"https://api.eia.gov/v2/electricity/rto/region-data/data/?frequency=hourly&data[0]=value&sort[0][column]=period&sort[0][direction]=desc&offset={start_offset}&length=5000&api_key=q5n29GJXkd5xd0nznZ9ZSfLwUSfA70oUP2WLaZhy"
    response = requests.get(url)
    json_data = response.json()
    start_offset += 5000
    
    df_data = json_data['response']['data']
    elec_data = pd.DataFrame(df_data)
    elec_data['value'] = pd.to_numeric(elec_data['value'],errors='coerce')
    elec_data['period'] = pd.to_datetime(elec_data['period'],errors='coerce')
    # insert_data = list(elec_data.itertuples(index=False, name=None))
    
    # cur.executemany(insert_query, insert_data)
    # conn.commit()

    print(f"Inserted rows {len(insert_data)} to postgres, currently at offset {start_offset}")

# engine = create_engine(f'postgresql+psycopg2://{db_user}:{db_password}@{db_host}:{db_port}/{db_name}')
# df_table.to_sql('profit_loss_data', engine, if_exists='replace', index=False)

OperationalError: connection to server at "192.168.1.188", port 5432 failed: Connection timed out (0x0000274C/10060)
	Is the server running on that host and accepting TCP/IP connections?


In [250]:
from sqlalchemy import create_engine

# 
# %%time

import requests
import pandas as pd
import psycopg2

all_data = []
start_offset = 0
url = "https://api.eia.gov/v2/electricity/rto/region-data/data/?frequency=hourly&data[0]=value&sort[0][column]=period&sort[0][direction]=desc&offset=0&length=0&api_key=q5n29GJXkd5xd0nznZ9ZSfLwUSfA70oUP2WLaZhy"

response = requests.get(url)
json_data = response.json()

total_record = 11000 #int(json_data['response']['total'])


db_params = {
    'dbname': 'reliance',
    'user': 'docker',
    'password': 'docker',
    'host': "localhost",
    'port': 5432
}

engine = create_engine(f"postgresql+psycopg2://{db_params['user']}:{db_params['password']}@{db_params['host']}:{db_params['port']}/{db_params['dbname']}")

while start_offset < total_record:
    url = f"https://api.eia.gov/v2/electricity/rto/region-data/data/?frequency=hourly&data[0]=value&sort[0][column]=period&sort[0][direction]=desc&offset={start_offset}&length=5000&api_key=q5n29GJXkd5xd0nznZ9ZSfLwUSfA70oUP2WLaZhy"
    response = requests.get(url)
    json_data = response.json()
    start_offset += 5000
    
    df_data = json_data['response']['data']
    elec_data = pd.DataFrame(df_data)
    elec_data['value'] = pd.to_numeric(elec_data['value'],errors='coerce')
    print(elec_data.head(1))
    elec_data.to_sql('test', engine, if_exists='append', index=False)
    

    print(f" currently at offset {start_offset}")

          period respondent     respondent-name type  \
0  2024-10-04T07        AVA  Avista Corporation   DF   

                   type-name  value    value-units  
0  Day-ahead demand forecast   1151  megawatthours  
 currently at offset 5000
          period respondent respondent-name type       type-name  value  \
0  2024-10-02T21        CAL      California   NG  Net generation   6743   

     value-units  
0  megawatthours  
 currently at offset 10000
          period respondent                             respondent-name type  \
0  2024-10-02T03       BANC  Balancing Authority of Northern California   NG   

        type-name  value    value-units  
0  Net generation   2718  megawatthours  
 currently at offset 15000


In [33]:
# all_data

elec_data = pd.DataFrame(all_data)
elec_data['value'] = pd.to_numeric(elec_data['value'])
elec_data.head()

period respondent                                 respondent-name  \
0  2024-09-20T07        AVA                              Avista Corporation   
1  2024-09-20T07       AZPS                  Arizona Public Service Company   
2  2024-09-20T07       BPAT                 Bonneville Power Administration   
3  2024-09-20T07        CAL                                      California   
4  2024-09-20T07       CHPD  Public Utility District No. 1 of Chelan County   

  type                  type-name  value    value-units  
0   DF  Day-ahead demand forecast   1139  megawatthours  
1   DF  Day-ahead demand forecast   3712  megawatthours  
2   DF  Day-ahead demand forecast   5399  megawatthours  
3   DF  Day-ahead demand forecast  27445  megawatthours  
4   DF  Day-ahead demand forecast    154  megawatthours

In [6]:
import pandas as pd

df_data = data['response']['data']
elec_data = pd.DataFrame(df_data)
elec_data['value'] = pd.to_numeric(elec_data['value'])
elec_data['period'] = pd.to_datetime(elec_data['period'])
insert_data = list(elec_data.itertuples(index=False, name=None))
insert_data

[(Timestamp('2024-09-25 07:00:00'),
  'AVA',
  'Avista Corporation',
  'DF',
  'Day-ahead demand forecast',
  1175,
  'megawatthours'),
 (Timestamp('2024-09-25 07:00:00'),
  'AZPS',
  'Arizona Public Service Company',
  'DF',
  'Day-ahead demand forecast',
  4278,
  'megawatthours'),
 (Timestamp('2024-09-25 07:00:00'),
  'BANC',
  'Balancing Authority of Northern California',
  'DF',
  'Day-ahead demand forecast',
  2268,
  'megawatthours'),
 (Timestamp('2024-09-25 07:00:00'),
  'BPAT',
  'Bonneville Power Administration',
  'DF',
  'Day-ahead demand forecast',
  5639,
  'megawatthours'),
 (Timestamp('2024-09-25 07:00:00'),
  'CAL',
  'California',
  'DF',
  'Day-ahead demand forecast',
  33905,
  'megawatthours'),
 (Timestamp('2024-09-25 07:00:00'),
  'CHPD',
  'Public Utility District No. 1 of Chelan County',
  'DF',
  'Day-ahead demand forecast',
  165,
  'megawatthours'),
 (Timestamp('2024-09-25 07:00:00'),
  'CISO',
  'California Independent System Operator',
  'DF',
  'Day-ahead 

In [12]:
import requests

url = "https://api.eia.gov/v2/co2-emissions/co2-emissions-aggregates/data/"
params = {
    'frequency': 'annual',
    'data[0]': 'value',
    'sort[0][column]': 'period',
    'sort[0][direction]': 'desc',
    'offset': 0,
    'length': 5000,
    'api_key': 'q5n29GJXkd5xd0nznZ9ZSfLwUSfA70oUP2WLaZhy'  
}

response = requests.get(url, params=params)


if response.status_code == 200:

    data = response.json()
    print("Data retrieved successfully:\n")
    print([json.dumps(json_data)])  
else:
    print(f"Failed to retrieve data. Status code: {response.status_code}")

# for record in data:
#     print(record)

Data retrieved successfully:

['{"response": {"warnings": [{"warning": "incomplete return", "description": "The API can only return 5000 rows in JSON format.  Please consider constraining your request with facet, start, or end, or using offset to paginate results."}], "total": "4073787", "dateFormat": "YYYY-MM-DD", "frequency": "daily", "data": [{"period": "2024-09-29", "respondent": "AECI", "respondent-name": "Associated Electric Cooperative, Inc.", "fueltype": "COL", "type-name": "Coal", "timezone": "Central", "timezone-description": "Central", "value": "32648", "value-units": "megawatthours"}, {"period": "2024-09-29", "respondent": "AECI", "respondent-name": "Associated Electric Cooperative, Inc.", "fueltype": "COL", "type-name": "Coal", "timezone": "Eastern", "timezone-description": "Eastern", "value": "32648", "value-units": "megawatthours"}, {"period": "2024-09-29", "respondent": "AECI", "respondent-name": "Associated Electric Cooperative, Inc.", "fueltype": "NG", "type-name": "N

In [7]:
df = pd.DataFrame(data['response']['data'])
df

period sectorId                                      sector-name fuelId  \
0      2021       RC             Residential carbon dioxide emissions     CO   
1      2021       TT  Total carbon dioxide emissions from all sectors     NG   
2      2021       TT  Total carbon dioxide emissions from all sectors     PE   
3      2021       TT  Total carbon dioxide emissions from all sectors     CO   
4      2021       TT  Total carbon dioxide emissions from all sectors     TO   
...     ...      ...                                              ...    ...   
4995   2017       CC              Commercial carbon dioxide emissions     PE   
4996   2017       CC              Commercial carbon dioxide emissions     CO   
4997   2017       RC             Residential carbon dioxide emissions     TO   
4998   2017       RC             Residential carbon dioxide emissions     NG   
4999   2017       RC             Residential carbon dioxide emissions     PE   

        fuel-name stateId            state-name     value  \
0            Coal      SC        South Carolina         0   
1     Natural Gas      DC  District of Columbia  1.499258   
2       Petroleum      DC  District of Columbia  1.021598   
3            Coal      DC  District of Columbia         0   
4       All Fuels      DC  District of Columbia  2.520856   
...           ...     ...                   ...       ...   
4995    Petroleum      AK                Alaska   .566578   
4996         Coal      AK                Alaska   .683419   
4997    All Fuels      AK                Alaska   1.66098   
4998  Natural Gas      AK                Alaska    1.0582   
4999    Petroleum      AK                Alaska    .60278   

                     value-units  
0     million metric tons of CO2  
1     million metric tons of CO2  
2     million metric tons of CO2  
3     million metric tons of CO2  
4     million metric tons of CO2  
...                          ...  
4995  million metric tons of CO2  
4996  million metric tons of CO2  
4997  million metric tons of CO2  
4998  million metric tons of CO2  
4999  million metric tons of CO2  

[5000 rows x 9 columns]

### CO2 Emission data

In [55]:
%%time

# Required lib requests pyscopg2 json pandas

import requests
import psycopg2
import json


start_offset = 0
url_temp = "https://api.eia.gov/v2/co2-emissions/co2-emissions-aggregates/data/?frequency=annual&data[0]=value&sort[0][column]=period&sort[0][direction]=desc&offset={}&length=5000&api_key=q5n29GJXkd5xd0nznZ9ZSfLwUSfA70oUP2WLaZhy"
url = url_temp.format(start_offset)
response = requests.get(url)
json_data = response.json()

total_record = 11000 #int(json_data['response']['total'])


db_params = {
    'dbname': 'reliance',
    'user': 'docker',
    'password': 'docker',
    'host': "192.168.1.188",
    'port': 5432
}


conn = psycopg2.connect(**db_params)

cur = conn.cursor()

create_table_query = '''
CREATE TABLE IF NOT EXISTS CO2_Emission_api_data (
id SERIAL PRIMARY KEY,
data JSONB
);
'''

cur.execute(create_table_query)
conn.commit()
print("Table created")

insert_query = '''
INSERT INTO CO2_Emission_api_data (data)
VALUES (%s)
'''


while start_offset < total_record:
    url = url_temp.format(start_offset)
    response = requests.get(url)
    json_data = response.json()
    start_offset += 5000

    cur.execute(insert_query, [json.dumps(json_data)])
    conn.commit()

    print(f"Currently at offset {start_offset}")



Table created
https://api.eia.gov/v2/co2-emissions/co2-emissions-aggregates/data/?frequency=annual&data[0]=value&sort[0][column]=period&sort[0][direction]=desc&offset=0&length=5000&api_key=q5n29GJXkd5xd0nznZ9ZSfLwUSfA70oUP2WLaZhy
Currently at offset 5000
https://api.eia.gov/v2/co2-emissions/co2-emissions-aggregates/data/?frequency=annual&data[0]=value&sort[0][column]=period&sort[0][direction]=desc&offset=5000&length=5000&api_key=q5n29GJXkd5xd0nznZ9ZSfLwUSfA70oUP2WLaZhy
Currently at offset 10000
https://api.eia.gov/v2/co2-emissions/co2-emissions-aggregates/data/?frequency=annual&data[0]=value&sort[0][column]=period&sort[0][direction]=desc&offset=10000&length=5000&api_key=q5n29GJXkd5xd0nznZ9ZSfLwUSfA70oUP2WLaZhy
Currently at offset 15000
CPU times: total: 1.48 s
Wall time: 10 s


In [55]:
from sqlalchemy import create_engine
import pandas as pd


db_params = {
    'dbname': 'reliance',
    'user': 'docker',
    'password': 'docker',
    'host': "localhost",
    'port': 5432
}


conn_string = f"postgresql+psycopg2://{db_params['user']}:{db_params['password']}@{db_params['host']}:{db_params['port']}/{db_params['dbname']}"
engine = create_engine(conn_string)


tables = ['co2_emi_api','eng_gen_api','Ren_cap_api']


def base_transform(table):  
    query = f'SELECT * FROM "{table}";'  
    df = pd.read_sql(query, engine)
    df = df.drop_duplicates()
    return df

co2_emi = base_transform(tables[0])
eng_gen = base_transform(tables[1])
Ren_cap = base_transform(tables[2])

###########################################################################################################
#CO2 Emissions by Energy Source
co2_emi[['period','stateId','fuelId','value']].rename(columns={'value': 'CO2_Emission_MMT'})


###########################################################################################################
#Energy Generation by Source** (from the **Electric Power Generation by Energy Source
def fueltype_calculation(row):
    value = float(row['generation_MWh'])  
    if row['fueltype'] == 'COL':
        return value * 1.03
    elif row['fueltype'] == 'NG':
        return value * 0.42
    elif row['fueltype'] == 'OIL':
        return value * 0.93
    else:
        return 0

eng_gen['value'] = pd.to_numeric(eng_gen['value'],errors='coerce')
eng_gen['period'] = pd.to_datetime(eng_gen['period'],errors='coerce')
eng_gen = eng_gen[['period','fueltype','respondent','value']].rename(columns={'value': 'generation_MWh'})
eng_gen['co2_emission_tons'] = eng_gen.apply(fueltype_calculation, axis=1)
eng_gen

###########################################################################################################
#Renewable Energy Adoption Rates
Ren_cap = Ren_cap[Ren_cap['activityName']=='Capacity']
Ren_cap['value'] = Ren_cap['value']/1000
Ren_cap[['period','countryRegionId','productName','value']].rename(columns={'value': 'CO2_Emission_MMT'})

###########################################################################################################


period fueltype respondent  generation_MWh  co2_emission_tons
0     2024-10-07      COL       AECI           31751           32703.53
1     2024-10-07      COL       AECI           31751           32703.53
2     2024-10-07       NG       AECI           12893            5415.06
3     2024-10-07       NG       AECI           12893            5415.06
4     2024-10-07      WND       AECI            6629               0.00
...          ...      ...        ...             ...                ...
24995 2024-09-24      OIL         NW            1222            1136.46
24996 2024-09-24      OIL         NW            1244            1156.92
24997 2024-09-24      OIL         NW            1186            1102.98
24998 2024-09-24      OIL         NW            1150            1069.50
24999 2024-09-24      OTH         NW           26883               0.00

[25000 rows x 5 columns]

In [39]:
eng_gen['year'] = eng_gen['period'].dt.year

In [29]:
def partition(year):
    df = eng_gen[eng_gen['year'] == year]
    df.to_sql(f'eng_gen_{year}' , engine_p, if_exists='append', index=False)

In [30]:
years = list(eng_gen['year'].unique())


db_params = {
    'dbname': 'postgres',
    'user': 'docker',
    'password': 'docker',
    'host': "localhost",
    'port': 5432
}


conn_string = f"postgresql+psycopg2://{db_params['user']}:{db_params['password']}@{db_params['host']}:{db_params['port']}/{db_params['dbname']}"
engine_p = create_engine(conn_string)
for year in years:
    partition(year)

In [13]:
%%time

import requests
import psycopg2
import json

apis = {
    "co2_emi_api": "https://api.eia.gov/v2/co2-emissions/co2-emissions-aggregates/data/?frequency=annual&data[0]=value&sort[0][column]=period&sort[0][direction]=desc",
    "eng_gen_api": "https://api.eia.gov/v2/international/data/?frequency=annual&data[0]=value&facets[activityId][]=7&facets[productId][]=29&facets[unit][]=MK&sort[0][column]=period&sort[0][direction]=desc",
    "Ren_cap_api": "https://api.eia.gov/v2/electricity/rto/daily-fuel-type-data/data/?frequency=daily&data[0]=value&sort[0][column]=period&sort[0][direction]=desc"
}

for key, value in apis.items():
    print(key)
    offset = 0 
    params = {
        'length': 5000,
        'api_key': 'q5n29GJXkd5xd0nznZ9ZSfLwUSfA70oUP2WLaZhy'
    }

    #Getting the total records
    params['offset'] = offset
    response = requests.get(value, params=params)
    json_data = response.json()
    total_record = int(json_data['response']['total'])

    db_params = {
    'dbname': 'reliance',
    'user': 'docker',
    'password': 'docker',
    'host': "localhost",
    'port': 5432
    }
    
    
    conn = psycopg2.connect(**db_params)
    
    cur = conn.cursor()
    
    create_table_query = f'''
    CREATE TABLE IF NOT EXISTS {key} (
    id SERIAL PRIMARY KEY,
    data JSONB
    );
    '''
    
    cur.execute(create_table_query)
    conn.commit()
    print(f"Created table for {key}")
    
    insert_query = f'''
    INSERT INTO {key} (data)
    VALUES (%s)
    '''

    while offset < 100: #total_record:
        params['offset'] = offset
        response = requests.get(value, params=params)
        
        if response.status_code == 200:
            data = response.json()
            print([json.dumps(data)])
            cur.execute(insert_query, [json.dumps(data)])
            conn.commit()
            print(f"Data retrieved successfully for {key} with offset {offset}:\n")
        else:
            print(f"Failed to retrieve data for {key}. Status code: {response.status_code}")
            break 
        
        offset += 5000 


co2_emi_api
Created table for co2_emi_api
['{"response": {"warnings": [{"warning": "incomplete return", "description": "The API can only return 5000 rows in JSON format.  Please consider constraining your request with facet, start, or end, or using offset to paginate results."}], "total": "64896", "dateFormat": "YYYY", "frequency": "annual", "data": [{"period": "2021", "sectorId": "RC", "sector-name": "Residential carbon dioxide emissions", "fuelId": "CO", "fuel-name": "Coal", "stateId": "SC", "state-name": "South Carolina", "value": "0", "value-units": "million metric tons of CO2"}, {"period": "2021", "sectorId": "TT", "sector-name": "Total carbon dioxide emissions from all sectors", "fuelId": "NG", "fuel-name": "Natural Gas", "stateId": "DC", "state-name": "District of Columbia", "value": "1.499258", "value-units": "million metric tons of CO2"}, {"period": "2021", "sectorId": "TT", "sector-name": "Total carbon dioxide emissions from all sectors", "fuelId": "PE", "fuel-name": "Petrole

## SPARQL

In [3]:
import requests


query = """
PREFIX bds: <http://www.bigdata.com/rdf/search#>
SELECT ?identifier ?value
WHERE {
    ?value bds:search 'Women' .
    ?value bds:matchAllTerms 'true' .
    ?identifier <http://www.loc.gov/mads/rdf/v1#authoritativeLabel> ?value .
}
"""


url = 'http://localhost:8889/bigdata/namespace/kb/sparql'


headers = {
    'Content-Type': 'application/sparql-query',
    'Accept': 'application/json'
}

response = requests.post(url, data=query, headers=headers)

if response.status_code == 200:
    print("Query executed successfully!")
    print("Response data:")
    print(response.json()) 
else:
    print(f"Failed to execute query. Status code: {response.status_code}")
    print("Response content:")
    print(response.text)


Query executed successfully!
Response data:
{'head': {'vars': ['identifier', 'value']}, 'results': {'bindings': [{'value': {'xml:lang': 'en', 'type': 'literal', 'value': 'Women'}, 'identifier': {'type': 'uri', 'value': 'http://id.loc.gov/authorities/childrensSubjects/sj96006385'}}, {'value': {'xml:lang': 'en', 'type': 'literal', 'value': 'Women in religion'}, 'identifier': {'type': 'uri', 'value': 'http://id.loc.gov/authorities/childrensSubjects/sj96006387'}}]}}


# Vscode Scripts

In [251]:
import requests
import psycopg2
import json
import os
from dotenv import load_dotenv

load_dotenv() 

base_url = 'https://api.eia.gov/v2/'

apis = {
    "co2_emi_api": f"{base_url}co2-emissions/co2-emissions-aggregates/data/?frequency=annual",
    "eng_gen_api": f"{base_url}electricity/rto/daily-fuel-type-data/data/?frequency=daily",
    "Ren_cap_api": f"{base_url}international/data/?frequency=annual&facets[activityId][]=12&facets[activityId][]=7&facets[productId][]=29&facets[countryRegionId][]=USA"
}

for key, value in apis.items():
    print(key)
    offset = 0 
    params = {
        'data[0]':'value',
        'length': 5000,
        'api_key':os.getenv("API_KEY") 
    }

    #Getting the total records
    params['offset'] = offset
    response = requests.get(value, params=params)
    json_data = response.json()
    total_record = int(json_data['response']['total'])

    db_params = {
    'dbname': os.getenv("DB"),
    'user': os.getenv("POST_USER"),
    'password': os.getenv("POST_PASS"),
    'host': os.getenv("HOST"),
    'port': os.getenv("PORT")
    }
    
    conn = psycopg2.connect(**db_params)
    cur = conn.cursor()
    
    create_table_query = f'''
    CREATE TABLE IF NOT EXISTS {key} (
    id SERIAL PRIMARY KEY,
    data JSONB
    );
    '''
    
    cur.execute(create_table_query)
    conn.commit()
    print(f"Created table for {key}")
    
    insert_query = f'''
    INSERT INTO {key} (data)
    VALUES (%s)
    '''

    no_rec = 0
    if total_record>20001:
        no_rec = 20001
    else:
        no_rec = total_record

    while offset < no_rec: #total_record:
        params['offset'] = offset
        response = requests.get(value, params=params)
        
        if response.status_code == 200:
            data = response.json()
            extracted_data = data['response']['data']
            cur.execute(insert_query, [json.dumps(extracted_data)])
            conn.commit()
            print(f"Data loaded successfully for {key} with offset {offset}:\n")
        else:
            print(f"Failed to retrieve data for {key}. Status code: {response.status_code}")
            break 
        
        offset += 5000

conn.close() 
cur.close()


co2_emi_api


Exception during reset or similar
Traceback (most recent call last):
  File "C:\Users\NaveenKushwaha\anaconda3\Lib\site-packages\sqlalchemy\pool\base.py", line 988, in _finalize_fairy
    fairy._reset(
  File "C:\Users\NaveenKushwaha\anaconda3\Lib\site-packages\sqlalchemy\pool\base.py", line 1438, in _reset
    pool._dialect.do_rollback(self)
  File "C:\Users\NaveenKushwaha\anaconda3\Lib\site-packages\sqlalchemy\engine\default.py", line 692, in do_rollback
    dbapi_connection.rollback()
psycopg2.OperationalError: could not receive data from server: Software caused connection abort (0x00002745/10053)



Created table for co2_emi_api
Data loaded successfully for co2_emi_api with offset 0:

Data loaded successfully for co2_emi_api with offset 5000:

Data loaded successfully for co2_emi_api with offset 10000:



KeyboardInterrupt: 

In [ ]:
import requests
from sqlalchemy import create_engine
import pandas as pd
import secret
from concurrent.futures import ThreadPoolExecutor, as_completed
import hvac

base_url = 'https://api.eia.gov/v2/'
tables = ['co2_emi_api', 'eng_gen_api', 'Ren_cap_api']
apis = {
    # "co2_emi_api": f"{base_url}co2-emissions/co2-emissions-aggregates/data/?frequency=annual",
    "eng_gen_api": f"{base_url}electricity/rto/daily-fuel-type-data/data/?frequency=daily",
    # "Ren_cap_api": f"{base_url}international/data/?frequency=annual&facets[activityId][]=7&facets[productId][]=116&facets[productId][]=29&facets[productId][]=33&facets[productId][]=37&facets[countryRegionId][]=USA"
}

def schema_co2_emission(df):
    df = df[['period', 'stateId', 'fuelId', 'value']].rename(columns={'value': 'CO2_Emission_MMT'})
    return df

def schema_energy_generation(df):
    df = df[['period', 'fueltype', 'respondent', 'value']].rename(columns={'value': 'generation_MWh'})
    return df

def schema_renewable_capacity(df):
    df = df[['period', 'countryRegionId', 'productName', 'value']].rename(columns={'value': 'CO2_Emission_MK'})
    return df

for key, value in apis.items():
    print(key)
    offset = 0
    params = {
        'data[0]': 'value',
        'length': 5000,
        'api_key': secret.API_KEY
    }

    # Getting the total records
    params['offset'] = offset
    response = requests.get(value, params=params)
    json_data = response.json()
    total_record = int(json_data['response']['total'])

    db_params = {
        'dbname': secret.DB,
        'user': secret.POST_USER,
        'password': secret.POST_PASS,
        'host': secret.HOST,
        'port': secret.PORT
    }

    engine = create_engine(f"postgresql+psycopg2://{db_params['user']}:{db_params['password']}@{db_params['host']}:{db_params['port']}/postgres")

    offsets = range(0, total_record, 5000)

    with ThreadPoolExecutor(max_workers=5) as executor:
        future_to_offset = {}
        
        for offset in offsets:
            params['offset'] = offset
            future = executor.submit(requests.get, value, params)
            future_to_offset[future] = offset

        for future in as_completed(future_to_offset):
            offset = future_to_offset[future]
            try:
                response = future.result()
                if response.status_code == 200:
                    data = response.json()
                    df = data['response']['data']
                    df = pd.DataFrame(df)
                    df['value'] = pd.to_numeric(df['value'], errors='coerce')

                    if key == tables[0]:
                        df = schema_co2_emission(df)
                    if key == tables[1]:
                        df = schema_energy_generation(df)
                    if key == tables[2]:
                        df = schema_renewable_capacity(df)

                    # df.to_sql(key, engine, if_exists='append', index=False)
                    print(f"Data loaded successfully for {key} with offset {offset}")
                else:
                    df = pd.DataFrame({'table': [key], 'offset': [offset], 'error': [response.status_code]})
                    # df.to_sql('Failed_import_api', engine, if_exists='append', index=False)
                    print(f"Failed to retrieve data for {key}. At Offset {offset} with Status code: {response.status_code}")
            except Exception as e:
                print(f"Error retrieving data for offset {offset}: {e}")


eng_gen_api
Data loaded successfully for eng_gen_api with offset 15000
Data loaded successfully for eng_gen_api with offset 5000
Data loaded successfully for eng_gen_api with offset 10000
Data loaded successfully for eng_gen_api with offset 0
Data loaded successfully for eng_gen_api with offset 20000
Data loaded successfully for eng_gen_api with offset 45000
Data loaded successfully for eng_gen_api with offset 25000
Data loaded successfully for eng_gen_api with offset 50000
Data loaded successfully for eng_gen_api with offset 30000
Data loaded successfully for eng_gen_api with offset 40000
Data loaded successfully for eng_gen_api with offset 55000
Data loaded successfully for eng_gen_api with offset 65000
Data loaded successfully for eng_gen_api with offset 60000
Data loaded successfully for eng_gen_api with offset 70000
Data loaded successfully for eng_gen_api with offset 75000
Data loaded successfully for eng_gen_api with offset 80000
Data loaded successfully for eng_gen_api with off

In [11]:
def create_chunks(total):
    chunks = []
    chunk_size = 1000000 

    for i in range(0, total + 1, chunk_size):
        chunks.append(i)

    if total not in chunks:
        chunks.append(total)

    return chunks

In [12]:
total_record = 4010000

if total_record>1000000:
    list_praser = create_chunks(total_record)
    for i in range(len(list_praser)-1):
        print(range(list_praser[i], list_praser[i+1], 5000))
    pass
else:
    offsets = range(0, total_record, 5000)
    print(offsets)

range(0, 1000000, 5000)
range(1000000, 2000000, 5000)
range(2000000, 3000000, 5000)
range(3000000, 4000000, 5000)
range(4000000, 4010000, 5000)


In [15]:
l = []

for i in range(4000000, 4010000, 5000):
    l.append(i)
l

[4000000, 4005000]